In [9]:
import numpy as np
import random

In [10]:
import networkx as nx
G = nx.read_edgelist(r"..\vertex_cover_benchmarks\ENZYMES_g102.edges", nodetype=int)

In [11]:
#MAX_FITNESS = G.order() # Tal y como está definido, el máximo valor que puede tomar el fitness es el número de nodos del grafo
MAX_FITNESS = 1
MAX_ITER = 10
SAMPLE_SIZE = 100
INITIAL_SAMPLE_SIZE = 300

In [12]:
class Solution:
    def __init__(self, sol, f = 0):
        self.sol = sol
        self.f = f

    def set_f(self, f):
        self.f = f

In [13]:
def subsets(a):
  l = len(a)
  n = l - 1
  x = [0] * n
  f = [j for j in range(l)]
  r = list()
  
  while n:
    m = [0] + x # insert 0 at the beginning of the bit string forms
    subset = [a[i] for i in range(l) if m[i] == 1] # generate the subset
    
    # and use the subset to generate the subsets for when 1 is inserted at the beginning
    k = [a[0]] + subset
    
    r.append(subset) # add to the table all subsets of bits strigs with prefix 0
    r.append(k) # add to the table all subsets of bits strings with prefix 1
    
    # initialization
    # this is where we choose which j we want to change
    j = f[0]
    f[0] = 0
    
    # if j == n we terminate because we have all the possible bit strings
    if j == n:
      break
     
    # update our array when j != n
    f[j] = f[j + 1]
    f[j + 1] = j + 1
    
    x[j] = 1 - x[j] # complement coordinate j and return to line 8 if j != n
  
  return r

In [14]:
def is_cover(sol, G):
    for u, v in G.edges():
        if sol[u - 1] == 0 and sol[v - 1] == 0:
            return False
    return True

In [15]:
def naive_cover(sol, G):
    for u, v in G.edges():
        if sol[u - 1] == 0 and sol[v - 1] == 0:
            sol[u - 1] = 1
    return

In [16]:
def fitness(sol):
    print("oye por favor")
    n = G.order()
    if is_cover(sol, G):
        return n - sum(sol)
    else:
        if sum(sol) >= (2 * n // 3):
            print("estoy en sitio bueno")
            zeros_index = []
            for i in range(len(sol)):
                if sol[i] == 0:
                    zeros_index.append(i)
                    #sol[i] = 1
                    #if is_cover(sol, G):
                    #    print(sol)
                    #    break
                    #sol[i] = 0
            r = subsets(zeros_index)
            r.sort(key=len)
            # r[0] es el conjunto vacío
            for subset in r[1:]:
                for index in subset:
                    sol[index] = 1 # Esto modifica sol porque se pasa por referencia
                if is_cover(sol, G):
                    print(f"found fitness {n - sum(sol)}")
                    return n - sum(sol)
                for index in subset:
                    sol[index] = 0
            #print("calavera 1")
            return 0
        else:
            naive_cover(sol, G)
            #print("calavera 2")
            return n - sum(sol)

In [17]:
(G.order() - 10) / G.order()

0.7619047619047619

In [18]:
def fitness2(sol):
    if is_cover(sol, G):
        print("found")
        n = G.order()
        return (n - sum(sol)) / n
    else:
        return 0

In [19]:
def fitness3(sol):
    n = G.order()
    if is_cover(sol, G):
        return (n - sum(sol)) / sum(sol)
    else:
        if sum(sol) >= (2 * n // 3):
            print("estoy en sitio bueno")
            zeros_index = []
            for i in range(len(sol)):
                if sol[i] == 0:
                    zeros_index.append(i)
                    #sol[i] = 1
                    #if is_cover(sol, G):
                    #    print(sol)
                    #    break
                    #sol[i] = 0
            r = subsets(zeros_index)
            r.sort(key=len)
            # r[0] es el conjunto vacío
            for subset in r[1:]:
                for index in subset:
                    sol[index] = 1 # Esto modifica sol porque se pasa por referencia
                if is_cover(sol, G):
                    print(f"found fitness {(n - sum(sol)) / sum(sol)}")
                    return (n - sum(sol)) / sum(sol)
                for index in subset:
                    sol[index] = 0
            assert(False)
            naive_cover(sol, G) # Pensándolo, aquí no debería llegar porque siempre se puede completar
            print("calavera 1")
            return (n - sum(sol)) / sum(sol)
        else:
            naive_cover(sol, G)
            #print("calavera 2")
            return (n - sum(sol)) / sum(sol)

In [20]:
def f(sol):
    fit = fitness3(sol.sol)
    sol.set_f(fit)
    #print(f"FITNESS de {sol.sol} = {fit}")
    return fit

In [21]:
def hamming_distance(sol1, sol2):
    n = len(sol1)
    #print(f"sol1 = {sol1}\nsol2 = {sol2}")
    assert(n == len(sol2))
    return [sol1[i] == sol2[i] for i in range(n)].count(False)

In [22]:
def inverse_distance(sol1, sol2, dist):
    d = dist(sol1, sol2)
    return 1 / d if d != 0 else 2 # Realmente la forma de manejar el infinito depende de la distancia
# El 2 funciona para Hammings porque no puede haber distancias d 0 < d < 1 (es decir, tales que 1 / d > 2).

In [23]:
inverse_distance([1,0,1,0], [0,1,0,1], hamming_distance)

0.25

In [24]:
def w(sol1, sol2, A, dist):
    assert(len(sol1) == len(sol2))
    sum = 0
    for point in A:
        sol = point.sol
        assert(len(sol) == len(sol1))
        sum += inverse_distance(sol1, sol, dist)
    assert(sum > 0) # Creo que se puede demostrar que esto no va a ser 0.
    inv = inverse_distance(sol1, sol2, dist)
    res = inv / sum
    #print(f"inv: {inv}\nsum: {sum}\nres: {res}")
    return res

In [25]:
def g(sol, A, dist):
    sum = 0
    for point in A:
        wei = w(sol.sol, point.sol, A, dist)
        fit = point.f
        #print(f"\nwei: {wei} \n fit: {fit}")
        sum += wei * fit
    print(f"\n\n g: {sum}\n\n")
    return sum

In [26]:
def sample(k, A, dist, skip = []):
    n = G.order()
    sample = []
    while len(sample) < k:
        x = [random.choice([0, 1]) for _ in range(n)]
        if x in sample or x in skip:
            continue
        #y = random.randint(0, MAX_FITNESS)
        y = random.uniform(0, MAX_FITNESS)
        sol = Solution(x)
        g_val = g(sol, A, dist)
        if g_val > y:
            #print(fitness(x))
            f(sol)
            #print(f"Muestra añadida {x}\ncon valor de g: {g_val} y valor de y: {y}")
            sample.append(sol)
    return sample

In [27]:
def init(k):
    n = G.order()
    init = []
    while len(init) < k:
        x = [random.choice([0, 1]) for _ in range(n)]
        if not any(point.sol == x for point in init): # Esto se evita usando un set. Aún no tengo claro si necesito índices, o si el set es eficiente en python.
            sol = Solution(x)
            f(sol)
            init.append(sol)
    return init

def max_k_fitness(set_sols, k):
    sor = sorted([(fitness(elem), elem) for elem in set_sols])
    return [elem for (_,elem) in sor][-k:]

def max_fitness(set_sols):
    max_value = fitness(set_sols[0])
    max_elem = set_sols[0]
    for elem in set_sols[1:]:
        f = fitness(elem)
        if f > max_value:
            max_value = f
            max_elem = elem
    return max_elem, max_value

def next_gen(curr_gen, k):
    new = sample(k, skip = curr_gen)
    return max_k_fitness(curr_gen + new, k)

def algorithm():
    gen = init(SAMPLE_SIZE)
    for _ in range(MAX_ITER):
        gen = next_gen(gen, SAMPLE_SIZE)
    return max_fitness(gen)

In [28]:
def max_f(A):
    assert(len(A) > 0)
    max_value = A[0].f
    max_elem = A[0]
    for elem in A[1:]:
        fit = elem.f
        if fit > max_value:
            max_value = fit
            max_elem = elem
    return max_elem, max_value

In [29]:
def alg(sample_size, num_iter, initial_sample_size, dist):
    #dic.clear()
    A = init(initial_sample_size)
    for i in range(num_iter):
        print(f"iter {i}")
        A.extend(sample(sample_size, A, dist, skip = A))
    return max_f(A)

In [30]:
def next_step(k, A, dist):
    next = sample(k, A, dist, skip = A)
    return next

In [31]:
def alg2(sample_size, num_iter, dist):
    A = init(sample_size)
    for i in range(num_iter):
        print(f"iter {i}")
        A = next_step(sample_size, A, dist)
    return max_f(A)

In [32]:
elem, fit = alg2(sample_size = SAMPLE_SIZE, num_iter = MAX_ITER, dist = hamming_distance)
print(f'Máximo valor de fitness ({fit}) encontrado para {elem.sol}, con {sum(elem.sol)} nodos.')

print(is_cover(elem.sol, G))


### A partir de aquí son formas de rellenar


num_ceros = G.order() - sum(elem.sol)
print(num_ceros, "ceros")

iter 0


 g: 0.21586872063521745




 g: 0.2167307461438225




 g: 0.21643809301043138




 g: 0.2144176681771717




 g: 0.21655893203241983




 g: 0.21699096126993017




 g: 0.21613274654544148




 g: 0.2160872118193536




 g: 0.217215603467203




 g: 0.2177300458028752




 g: 0.2174186046845865




 g: 0.21705375586784978




 g: 0.2171397743632797




 g: 0.21755726173233986




 g: 0.21720086674048103




 g: 0.21790013716112316




 g: 0.21596913891477865




 g: 0.21609479857540023




 g: 0.21704489416049372




 g: 0.21676171044647358




 g: 0.2164203940761144




 g: 0.2163041441275583




 g: 0.2167131078378939




 g: 0.21756729493184224




 g: 0.2167595744925057




 g: 0.21682265185461186




 g: 0.21651513312895115




 g: 0.21663062437856534




 g: 0.21671406283964914




 g: 0.21766689386979202




 g: 0.21726272355437443




 g: 0.21828464878155956




 g: 0.2171563492895845




 g: 0.2168638249697914




 g: 0.21659778183999162




 g: 0.21736778149310343



In [33]:
output = open("medias_ponderadas_GA.txt", "a")
elem, fit = alg2(sample_size = SAMPLE_SIZE, num_iter = MAX_ITER, dist = hamming_distance)
output.write(f'Máximo valor de fitness ({fit}) encontrado para {elem.sol}, con {sum(elem.sol)} nodos.')


### A partir de aquí son formas de rellenar


num_ceros = G.order() - sum(elem.sol)
output.write(num_ceros, "ceros")
output.close()

estoy en sitio bueno
found fitness 0.23529411764705882
iter 0


 g: 0.2331946437515541




 g: 0.23125894535419103




 g: 0.23400994331229003




 g: 0.23506345119260486




 g: 0.2313491468279462




 g: 0.2326392174290366




 g: 0.23442285664345605




 g: 0.2340401255924092




 g: 0.23315999733750906




 g: 0.23093429018595338




 g: 0.23024387953522943


estoy en sitio bueno
found fitness 0.2727272727272727


 g: 0.23116336834209333




 g: 0.2333952820038905




 g: 0.23159240102918363




 g: 0.23309148669819246




 g: 0.23315237211488535




 g: 0.23407156720374597




 g: 0.23104760329094454




 g: 0.23276256607309603




 g: 0.2328079816282396




 g: 0.233491797668812




 g: 0.23226480618730147




 g: 0.2327339249214986




 g: 0.23348040512568202




 g: 0.234667544643909




 g: 0.23165604689853736




 g: 0.23149570053849355




 g: 0.23340912383529272




 g: 0.23423549256830878




 g: 0.23180942693155707




 g: 0.23351583739763673




 g: 0.23262290424841386



TypeError: write() argument must be str, not bool

In [42]:
output = open("medias_ponderadas_GA.csv", "a")
output.write(f'{elem.sol},')


### A partir de aquí son formas de rellenar


num_ceros = G.order() - sum(elem.sol)
output.write(f'{num_ceros}\n')
output.write(f'{elem.sol},')


### A partir de aquí son formas de rellenar


num_ceros = G.order() - sum(elem.sol)
output.write(f'{num_ceros}\n')
output.close()

In [46]:
output = open(r"..\results\medias_ponderadas.csv", "a")
for _ in range(20):
    elem, fit = alg2(sample_size = SAMPLE_SIZE, num_iter = MAX_ITER, dist = hamming_distance)
    output.write(f'{elem.sol},')

    num_ceros = G.order() - sum(elem.sol)
    output.write(f'{num_ceros}\n')

output.close()

estoy en sitio bueno
found fitness 0.3125
iter 0


 g: 0.22599237564368801




 g: 0.23023075627272407




 g: 0.23171326837192663




 g: 0.22898499725243754




 g: 0.22930047473360055




 g: 0.22821201864325866




 g: 0.23166255324678997




 g: 0.22980737943762775




 g: 0.23208422067086698




 g: 0.22778353363213202




 g: 0.23040098651721636




 g: 0.23048073193377314




 g: 0.23073513414152136




 g: 0.2311737454578657




 g: 0.230964535307018




 g: 0.22516944551111337




 g: 0.2302518576905091




 g: 0.22970649351593245




 g: 0.2294797199915884




 g: 0.23057483575691864




 g: 0.2293985921657383




 g: 0.22964390625038647




 g: 0.23010848083900548




 g: 0.23118058947505737




 g: 0.22781986967169038




 g: 0.23119834249381652




 g: 0.22865199638293196




 g: 0.22778741405940148




 g: 0.22877604644104538




 g: 0.2299319066202006




 g: 0.23028044333100248




 g: 0.22901670446188108




 g: 0.2283015940367898




 g: 0.23017267656747925




 g: 0